In [115]:
import json
import re
import nltk
from nltk.tokenize import RegexpTokenizer
from nltk.stem.wordnet import WordNetLemmatizer
from nltk import pos_tag
nltk.download('punkt')
nltk.download('averaged_perceptron_tagger')
from gensim.models import Phrases
from gensim.corpora import Dictionary
from gensim.models import LdaModel
from gensim.parsing.preprocessing import remove_stopwords
import pyLDAvis.gensim
#API Modules
import requests
import creds


#Text processing Modules
import string

from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords

#General Data processing Modules
import pandas as pd
import numpy as np
from typing import Dict, List
from collections import defaultdict

#Modules for checking for title similarity
from itertools import combinations
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity

# Modules for topic modeling
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.decomposition import LatentDirichletAllocation
import joblib


[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\chaub\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     C:\Users\chaub\AppData\Roaming\nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!


In [100]:
#Load model
lda = LdaModel.load('model.pkl')

dictionary = Dictionary.load('dictionary.pkl')
topic_dictionary = {
    0: "Politics",
    1: "Hard News",
    2: "Business",
    3: "Entertainment",
    4: "Community",
    5: "Technology",
    6: "Sports"
}



In [101]:
def predict_category(model, new_summaries):
    """
    Predicts the category for a new summary or a 
    list of new summaries using the trained LDA model.

    Args:
        model (LdaModel): Trained LDA model.
        new_summaries (List[str] or str): New summary or list of new summaries to predict the category for.

    Returns:
        predicted_topics (List[int] or int): Predicted topic index or list of predicted topic indices for the new summaries.
    """
    
    # Processing the new summaries to prepare them for gensim
    processed_summaries = process_for_gensim(new_summaries)

    # Creating a bag of work representation of new summaries
    new_bow = [dictionary.doc2bow(summary) for summary in processed_summaries]

    #Predict the topic distribution
    predicted_topics = [max(model.get_document_topics(bow), key = lambda item: item[1])[0] for bow in new_bow]

    predicted_topics = [topic_dictionary[topic] for topic in predicted_topics]
    
    return predicted_topics

In [102]:
with open('test_model.json') as file:
    d = file.read()

data = json.loads(d)
test_data = []
index = 0
for i in data['articles']:
    test_data.append(str(index)+str(i['summary']))
    index += 1


In [103]:
print(len(test_data))
test_data

345


['0"What we have once enjoyed we can never lose.\xa0\nAll that we love deeply becomes a part of us\n.\'\n~ Helen Keller\nSandra B. Vincent\n1946-2024\nSandy passed away surrounded by her loving family on January 29, 2024, in Las Vegas, Nevada.\nShe was born on July 16, 1946, to Paul Thomas Benner and Nina Barnett Benner In Kansas City, Missouri.\nShe moved with her family to Spring Lake, Utah, in 1948.\nShe married E. Brent Vincent on June 19, 1971, in Elko, Nevada.\nSandy and Brent moved to Henderson, Nevada, in September 1997 for the weather and to be close to their grand kids.\nShe spent 53 very happy years together with her husband. They spent their summers enjoying camping and fishing at Fishlake, Utah.\nShe was career woman who started at Commercial Security Bank (now Key Bank) as a teller in 1969 and retired in 1997 as a Senior Vice President. Sandy enjoyed watching basketball and baseball with Brent. She was an avid crafter, especially making cards with her stampin\' buddies. I

In [104]:
pred = predict_category(lda, test_data)
print(pred[:10])

[['what', 'enjoyed', 'lose', 'love', 'deeply', 'helen', 'keller', 'sandra', 'b', 'vincent', 'sandy', 'passed', 'away', 'surrounded', 'loving', 'family', 'january', 'las', 'vegas', 'nevada', 'born', 'july', 'paul', 'thomas', 'benner', 'nina', 'barnett', 'benner', 'kansas', 'city', 'missouri', 'moved', 'family', 'spring', 'lake', 'utah', 'married', 'e', 'brent', 'vincent', 'june', 'elko', 'nevada', 'sandy', 'brent', 'moved', 'henderson', 'nevada', 'september', 'weather', 'close', 'grand', 'kids', 'spent', 'happy', 'years', 'husband', 'spent', 'summers', 'enjoying', 'camping', 'fishing', 'fishlake', 'utah', 'career', 'woman', 'started', 'commercial', 'security', 'bank', 'now', 'key', 'bank', 'teller', 'retired', 'senior', 'vice', 'president', 'sandy', 'enjoyed', 'watching', 'basketball', 'baseball', 'brent', 'avid', 'crafter', 'especially', 'making', 'cards', 'stampin', 'buddies', 'watching', 'games', 'stampin', 'sandy', 'read', 'hands', 'on', 'sandy', 'loved', 'grandma', 'especially', 'g

In [105]:
print(pred)


['Hard News', 'Entertainment', 'Entertainment', 'Hard News', 'Politics', 'Hard News', 'Politics', 'Hard News', 'Hard News', 'Politics', 'Politics', 'Technology', 'Entertainment', 'Community', 'Hard News', 'Technology', 'Sports', 'Hard News', 'Sports', 'Hard News', 'Community', 'Hard News', 'Sports', 'Business', 'Politics', 'Community', 'Hard News', 'Hard News', 'Hard News', 'Business', 'Hard News', 'Hard News', 'Entertainment', 'Entertainment', 'Entertainment', 'Entertainment', 'Business', 'Entertainment', 'Entertainment', 'Entertainment', 'Entertainment', 'Entertainment', 'Hard News', 'Business', 'Hard News', 'Hard News', 'Hard News', 'Hard News', 'Sports', 'Hard News', 'Hard News', 'Hard News', 'Business', 'Politics', 'Hard News', 'Business', 'Hard News', 'Hard News', 'Entertainment', 'Hard News', 'Hard News', 'Hard News', 'Hard News', 'Sports', 'Hard News', 'Hard News', 'Hard News', 'Community', 'Hard News', 'Hard News', 'Politics', 'Business', 'Entertainment', 'Entertainment', 'Pol

In [106]:
test = ["I play basketball becaus eit is a fun sport", "I made a lot of money by selling my company to the fortune 500 company", "That music festival was so entertaining","That murderer was prosecuted by the judge","There was a robbery of 5th street, and the thieves were caught red handed"]
pred_2 = predict_category(lda, test)
print(pred_2)

[['play', 'basketball', 'becaus', 'eit', 'fun', 'sport'], ['lot', 'money', 'selling', 'company', 'fortune', 'company'], ['music', 'festival', 'entertaining'], ['murderer', 'prosecuted', 'judge'], ['robbery', '5th', 'street', 'thieves', 'caught', 'red', 'handed']]
5
['Entertainment', 'Business', 'Hard News', 'Community', 'Community']


In [107]:
processed_summaries = process_for_gensim(test)

    # Creating a bag of work representation of new summaries
new_bow = [dictionary.doc2bow(summary) for summary in processed_summaries]

AttributeError: 'list' object has no attribute 'lower'

In [ ]:
new_bow

[[(156, 1), (1111, 1), (1633, 1), (2207, 1)],
 [(197, 2), (1473, 1), (2411, 1), (4361, 1)],
 [(413, 1), (3241, 1)],
 [(3567, 1), (6203, 1)],
 [(67, 1), (161, 1), (533, 1), (1966, 1), (3943, 1), (5072, 1)]]

In [ ]:
topic_distributions = [lda.get_document_topics(bow) for bow in new_bow]

In [ ]:
topic_distributions

[[(0, 0.13545492),
  (1, 0.13519341),
  (2, 0.1351736),
  (3, 0.1756194),
  (4, 0.14642686),
  (5, 0.13668604),
  (6, 0.13544573)],
 [(0, 0.13944943),
  (1, 0.17646575),
  (2, 0.1407333),
  (3, 0.13412936),
  (4, 0.13623066),
  (5, 0.13477547),
  (6, 0.138216)],
 [(0, 0.13888995),
  (1, 0.13890725),
  (2, 0.13888995),
  (3, 0.13888995),
  (4, 0.166593),
  (5, 0.13893998),
  (6, 0.13888995)],
 [(0, 0.1389048),
  (1, 0.1388955),
  (2, 0.1665093),
  (3, 0.1388955),
  (4, 0.1388955),
  (5, 0.13900393),
  (6, 0.1388955)],
 [(0, 0.13709074),
  (1, 0.1320501),
  (2, 0.17383523),
  (3, 0.14697148),
  (4, 0.13786651),
  (5, 0.13829418),
  (6, 0.1338918)]]

In [109]:

def get_unique_indices(data):
    """
    This function checks the titles of each article, compares
    the similar groups and then picks the article with the 
    best rank, in this case the lowest rank. 

    Args:
        data (json): A json value of key 'articles', with more keys like 'title', 'rank' etc
    
    Returns:
        unique_indices (List): List of all indices that have completely unique 
                                titles.

    """

    titles = [entry['title'] for entry in data]
    ranks = [entry['rank'] for entry in data]

    # Compute similarity score between titles
    vectorizer = TfidfVectorizer()
    tfidf_matrix = vectorizer.fit_transform(titles)
    similarity_matrix = cosine_similarity(tfidf_matrix)

    # Setting similarity threshold
    cosine_sim_threshold = 0.8

    # Identify pairs of titles with high similarity scores
    similar_titles = []
    for i,j in combinations(range(len(titles)), 2):
        similarity_score = similarity_matrix[i,j]
        if similarity_score > cosine_sim_threshold:
            similar_titles.append((i,j))
    
    indices_in_similar_titles = set([item for sublist in similar_titles for item in sublist])
    json_full_indices = set(np.arange(len(data)))
    originally_unique_indices = list(json_full_indices-indices_in_similar_titles)

    sim_articles_dict = {}

    for idx1, idx2 in similar_titles:
        sim_articles_dict.setdefault(idx1, []). append(idx2)

    similar_groups = [sorted(sim_articles_dict[key]+[key]) for key in sim_articles_dict]

    best_article_indices = []

    # Iterating over list of list  of similar indices
    for group in similar_groups:

        # Creating an array to store the ranks of each index
        ranks_in_group = []

        # Iterating over each index of the list of similar indices
        for idx in group:
            rank = ranks[idx]
            ranks_in_group.append(rank)
        best_rank_idx = np.argmin(ranks_in_group)

        best_article_indices.append(group[best_rank_idx])

    unique_indices = originally_unique_indices+best_article_indices
    
    return unique_indices


def process_string(text):

    """
    This function processing raw string by making words lowercase
    removing punctuations, removing whitespace, special characters

    Args:
        text (str): Raw input string
    
    Return:
        text (str): String with punctuations, whitespaces, special characters removed.

    """

    # Making the text lower case
    text = text.lower() 

    # Removing punctuations
    translator = str.maketrans('', '', string.punctuation)
    text = text.translate(translator)

    # Removing whitespace
    text = " ".join(text.split())

    return text


def remove_url(string):

    url_pattern = re.compile(r'https?://\S+|www\.\S+')

    return url_pattern.sub('', string)



def process_for_gensim(docs):
    """
    This function prepares the summary to be used by the 
    gensim topic model for topic modeling

    Args:
        docs (List(str)): List of all summaries of articles 
                        fetched from API call

    Returns:
        processed_doc (List(List(str))): List of List of tokens of each
                                         summary with 
                                         necessary processing done

    """


    remove_these = {
    "new york", "los angeles", "chicago", "houston", "phoenix", "philadelphia", "san antonio",
    "san diego", "dallas", "san jose", "austin", "jacksonville", "san francisco", "columbus",
    "fort worth", "indianapolis", "charlotte", "seattle", "denver", "washington", "boston",
    "el paso", "nashville", "detroit", "oklahoma city", "portland", "las vegas", "memphis",
    "louisville", "baltimore", "milwaukee", "albuquerque", "tucson", "fresno", "sacramento",
    "kansas city", "long beach", "atlanta", "omaha", "raleigh", "miami", "oakland", "minneapolis",
    "tulsa", "wichita", "arlington", "new orleans", "cleveland", "bakersfield", "tampa",
    "alabama", "alaska", "arizona", "arkansas", "california", "colorado", "connecticut",
    "delaware", "florida", "georgia", "hawaii", "idaho", "illinois", "indiana", "iowa",
    "kansas", "kentucky", "louisiana", "maine", "maryland", "massachusetts", "michigan",
    "minnesota", "mississippi", "missouri", "montana", "nebraska", "nevada", "new hampshire",
    "new jersey", "new mexico", "new york", "north carolina", "north dakota", "ohio", "oklahoma",
    "oregon", "pennsylvania", "rhode island", "south carolina", "south dakota", "tennessee",
    "texas", "utah", "vermont", "virginia", "washington", "west virginia", "wisconsin", "wyoming",
    "al", "ak", "az", "ar", "ca", "co", "ct", "de", "fl", "ga", "hi", "id", "il", "in", "ia", "ks", 
    "ky", "la", "me", "md", "ma", "mi", "mn", "ms", "mo", "mt", "ne", "nv", "nh", "nj", "nm", "ny", 
    "nc", "nd", "oh", "ok", "or", "pa", "ri", "sc", "sd", "tn", "tx", "ut", "vt", "va", "wa", "wv", "wi", "wy","it",
    "i", "me", "my", "myself", "we", "our", "ours", "ourselves", "you", "your", "yours", "yourself", 
    "yourselves", "he", "him", "his", "himself", "she", "her", "hers", "herself", "it", "its", "itself", 
    "they", "them", "their", "theirs", "themselves", "what", "which", "who", "whom", "this", "that", "these", 
    "those", "am", "is", "are", "was", "were", "be", "been", "being", "have", "has", "had", "having", "do", 
    "does", "did", "doing", "a", "an", "the", "and", "but", "if", "or", "because", "as", "until", "while", 
    "of", "at", "by", "for", "with", "about", "against", "between", "into", "through", "during", "before", 
    "after", "above", "below", "to", "from", "up", "down", "in", "out", "on", "off", "over", "under", "again", 
    "further", "then", "once", "here", "there", "when", "where", "why", "how", "all", "any", "both", "each", 
    "few", "more", "most", "other", "some", "such", "no", "nor", "not", "only", "own", "same", "so", "than", 
    "too", "very", "s", "t", "can", "will", "just", "don", "should", "now", "january", "february", "march", "april", 
    "may", "june", "july", "august", "september", "october", "november", "december", "jan", "feb", "mar", "apr",
    "jun", "jul", "aug", "sep", "oct", "nov", "dec", "mon", "tue", "wed", "thu", "fri", "sat", "sunday", "monday", "tuesday","wednesday",
    "thursday", "saturday", "tork","orlando","city","like","want", "going","go","think","way", "come","say","look","good","know",
    "thing","work","need", "lot", "told", "day", "today", "re", "credit", "la", "people", "feel"

    }

    tokenizer = RegexpTokenizer(r'\w+')

    for idx in range(len(train_data)):
        # Convert to lowercase
        train_data[idx] = train_data[idx].lower()
        # Remove URLs
        train_data[idx] = remove_url(train_data[idx])
        # Remove stopwords
        train_data[idx] = remove_stopwords(train_data[idx])
        # Split into words
        train_data[idx] = tokenizer.tokenize(train_data[idx])

    # Remove numbers, but not words that contain numbers
    train_data = [[token for token in train_summary if not token.isnumeric()] for train_summary in train_data]
    print(train_data)

    # Remove words that are only one character
    train_data = [[token for token in train_summary if len(token) > 1] for train_summary in train_data]
    print(len(train_data))

    lemmatizer = WordNetLemmatizer()
    train_data = [[lemmatizer.lemmatize(token) for token in train_summary] for train_summary in train_data]

    # Remove all places in remove_these because city and state names are ruining the model
    train_data = [[token for token in train_summary if token not in remove_these] for train_summary in train_data]

    bigram = Phrases(train_data, min_count = 10)
    for idx in range(len(train_data)):
        for token in bigram[train_data[idx]]:
            if '_' in token:
                # Token is a bigram, add it to the document
                train_data[idx].append(token)
    
    return train_data

def predict_category(model, new_summaries):
    """
    Predicts the category for a new summary or a 
    list of new summaries using the trained LDA model.

    Args:
        model (LdaModel): Trained LDA model.
        new_summaries (List[str] or str): New summary or list of new summaries to predict the category for.

    Returns:
        predicted_topics (List[int] or int): Predicted topic index or list of predicted topic indices for the new summaries.
    """
    dictionary = Dictionary.load('dictionary.pkl')
    topic_dictionary = {
                        0: "Politics",
                        1: "Hard News",
                        2: "Business",
                        3: "Entertainment",
                        4: "Community",
                        5: "Technology",
                        6: "Sports"
                        }
    # Processing the new summaries to prepare them for gensim
    processed_summaries = process_for_gensim(new_summaries)

    # Creating a bag of work representation of new summaries
    new_bow = [dictionary.doc2bow(summary) for summary in processed_summaries]

    #Predict the topic distribution
    predicted_topics = [max(model.get_document_topics(bow), key = lambda item: item[1])[0] for bow in new_bow]

    predicted_topics = [topic_dictionary[topic] for topic in predicted_topics]
    
    return predicted_topics

def process_shrink_data(articles, location):
    """
    This function takes in the input that comes from a collection 
    in MongoDB. This function processes the important strings for
    each article in the document, removes any duplicate articles
    and adds a topic to each article using topic modeling model

    Arg:
        articles (List(json/dict)): A list of dictionaries/json where each json is an article
        location (str): The location used when querying to newscatcherAPI in the backend

    Returns:
        json(List(json))
    
    """
    
    # Loading the model and countvectorizer
    lda = LdaModel.load('model.pkl')


    location = location
    processed_articles = []
    
    for item in articles:
        
        #Condition to continue to next iteration if str present
        
        regex_pattern = rf'Reporting by .{{0,50}} in {location}'
        if re.search(regex_pattern, item.summary):
            continue

        #Get title
        title = process_string(item.title)
        
        #Get excerpt
        if item.excerpt == None:
            excerpt = "No excerpt for this article"
        else:
            excerpt = process_string(item.excerpt)
        
        
        processed_article = {
            "rank": int(item.rank),
            "location": location,
            "title": title,
            "excerpt": excerpt,
            "summary":item.summary,
            "link": item.link,
            "author": str(item.author),
            "published_date": item.published_date[:10],
            "image_link": item.media
        }
        
        processed_articles.append(processed_article)

    articles_json = {
        "articles": processed_articles
    }

    data = articles_json['articles']

    unique_indices = get_unique_indices(data)

    articles_json['articles'] = [articles_json['articles'][i] for i in unique_indices]
    
    summaries = [article['summary'] for article in articles_json['articles']]

    predictions = predict_category(model = lda, new_summaries=summaries)

    for article, prediction in zip(articles_json['articles'], predictions):
        article["topic"] = prediction

    

    #REMOVE BELOW PRINT STATEMENT WHEN DONE TESTING
    #print(len(articles_json['articles']))
    json_output = json.dumps(articles_json, ensure_ascii=False)

    return json_output


# This is for testing, Above is to move to functions.py

In [141]:


def process_string(text):

    """
    This function processing raw string by making words lowercase
    removing punctuations, removing whitespace, special characters

    Args:
        text (str): Raw input string
    
    Return:
        text (str): String with punctuations, whitespaces, special characters removed.

    """

    # Making the text lower case
    text = text.lower() 

    # Removing punctuations
    translator = str.maketrans('', '', string.punctuation)
    text = text.translate(translator)

    # Removing whitespace
    text = " ".join(text.split())

    text = text.title()

    return text


def get_unique_indices(data):
    """
    This function checks the titles of each article, compares
    the similar groups and then picks the article with the 
    best rank, in this case the lowest rank. 

    Args:
        data (json): A json value of key 'articles', with more keys like 'title', 'rank' etc
    
    Returns:
        unique_indices (List): List of all indices that have completely unique 
                                titles.

    """

    titles = [process_string(entry['title']) for entry in data]
    ranks = [entry['rank'] for entry in data]

    # Compute similarity score between titles
    vectorizer = TfidfVectorizer()
    tfidf_matrix = vectorizer.fit_transform(titles)
    similarity_matrix = cosine_similarity(tfidf_matrix)

    # Setting similarity threshold
    cosine_sim_threshold = 0.8

    # Identify pairs of titles with high similarity scores
    similar_titles = []
    for i,j in combinations(range(len(titles)), 2):
        similarity_score = similarity_matrix[i,j]
        if similarity_score > cosine_sim_threshold:
            similar_titles.append((i,j))
    
    indices_in_similar_titles = set([item for sublist in similar_titles for item in sublist])
    json_full_indices = set(np.arange(len(data)))
    originally_unique_indices = list(json_full_indices-indices_in_similar_titles)

    sim_articles_dict = {}

    for idx1, idx2 in similar_titles:
        sim_articles_dict.setdefault(idx1, []). append(idx2)

    similar_groups = [sorted(sim_articles_dict[key]+[key]) for key in sim_articles_dict]

    best_article_indices = []

    # Iterating over list of list  of similar indices
    for group in similar_groups:

        # Creating an array to store the ranks of each index
        ranks_in_group = []

        # Iterating over each index of the list of similar indices
        for idx in group:
            rank = ranks[idx]
            ranks_in_group.append(rank)
        best_rank_idx = np.argmin(ranks_in_group)

        best_article_indices.append(group[best_rank_idx])

    unique_indices = originally_unique_indices+best_article_indices
    
    return unique_indices



def remove_url(string):

    url_pattern = re.compile(r'https?://\S+|www\.\S+')

    return url_pattern.sub('', string)



def process_for_gensim(docs):
    """
    This function prepares the summary to be used by the 
    gensim topic model for topic modeling

    Args:
        docs (List(str)): List of all summaries of articles 
                        fetched from API call

    Returns:
        processed_doc (List(List(str))): List of List of tokens of each
                                         summary with 
                                         necessary processing done

    """


    remove_these = {
    "new york", "los angeles", "chicago", "houston", "phoenix", "philadelphia", "san antonio",
    "san diego", "dallas", "san jose", "austin", "jacksonville", "san francisco", "columbus",
    "fort worth", "indianapolis", "charlotte", "seattle", "denver", "washington", "boston",
    "el paso", "nashville", "detroit", "oklahoma city", "portland", "las vegas", "memphis",
    "louisville", "baltimore", "milwaukee", "albuquerque", "tucson", "fresno", "sacramento",
    "kansas city", "long beach", "atlanta", "omaha", "raleigh", "miami", "oakland", "minneapolis",
    "tulsa", "wichita", "arlington", "new orleans", "cleveland", "bakersfield", "tampa",
    "alabama", "alaska", "arizona", "arkansas", "california", "colorado", "connecticut",
    "delaware", "florida", "georgia", "hawaii", "idaho", "illinois", "indiana", "iowa",
    "kansas", "kentucky", "louisiana", "maine", "maryland", "massachusetts", "michigan",
    "minnesota", "mississippi", "missouri", "montana", "nebraska", "nevada", "new hampshire",
    "new jersey", "new mexico", "new york", "north carolina", "north dakota", "ohio", "oklahoma",
    "oregon", "pennsylvania", "rhode island", "south carolina", "south dakota", "tennessee",
    "texas", "utah", "vermont", "virginia", "washington", "west virginia", "wisconsin", "wyoming",
    "al", "ak", "az", "ar", "ca", "co", "ct", "de", "fl", "ga", "hi", "id", "il", "in", "ia", "ks", 
    "ky", "la", "me", "md", "ma", "mi", "mn", "ms", "mo", "mt", "ne", "nv", "nh", "nj", "nm", "ny", 
    "nc", "nd", "oh", "ok", "or", "pa", "ri", "sc", "sd", "tn", "tx", "ut", "vt", "va", "wa", "wv", "wi", "wy","it",
    "i", "me", "my", "myself", "we", "our", "ours", "ourselves", "you", "your", "yours", "yourself", 
    "yourselves", "he", "him", "his", "himself", "she", "her", "hers", "herself", "it", "its", "itself", 
    "they", "them", "their", "theirs", "themselves", "what", "which", "who", "whom", "this", "that", "these", 
    "those", "am", "is", "are", "was", "were", "be", "been", "being", "have", "has", "had", "having", "do", 
    "does", "did", "doing", "a", "an", "the", "and", "but", "if", "or", "because", "as", "until", "while", 
    "of", "at", "by", "for", "with", "about", "against", "between", "into", "through", "during", "before", 
    "after", "above", "below", "to", "from", "up", "down", "in", "out", "on", "off", "over", "under", "again", 
    "further", "then", "once", "here", "there", "when", "where", "why", "how", "all", "any", "both", "each", 
    "few", "more", "most", "other", "some", "such", "no", "nor", "not", "only", "own", "same", "so", "than", 
    "too", "very", "s", "t", "can", "will", "just", "don", "should", "now", "january", "february", "march", "april", 
    "may", "june", "july", "august", "september", "october", "november", "december", "jan", "feb", "mar", "apr",
    "jun", "jul", "aug", "sep", "oct", "nov", "dec", "mon", "tue", "wed", "thu", "fri", "sat", "sunday", "monday", "tuesday","wednesday",
    "thursday", "saturday", "tork","orlando","city","like","want", "going","go","think","way", "come","say","look","good","know",
    "thing","work","need", "lot", "told", "day", "today", "re", "credit", "la", "people", "feel"

    }

    tokenizer = RegexpTokenizer(r'\w+')

    for idx in range(len(docs)):
        # Convert to lowercase
        docs[idx] = docs[idx].lower()
        # Remove URLs
        docs[idx] = remove_url(docs[idx])
        # Remove stopwords
        docs[idx] = remove_stopwords(docs[idx])
        # Split into words
        docs[idx] = tokenizer.tokenize(docs[idx])

    # Remove numbers, but not words that contain numbers
    docs = [[token for token in train_summary if not token.isnumeric()] for train_summary in docs]
    #print(train_data)

    # Remove words that are only one character
    docs = [[token for token in train_summary if len(token) > 1] for train_summary in docs]
    #print(len(train_data))

    lemmatizer = WordNetLemmatizer()
    docs = [[lemmatizer.lemmatize(token) for token in train_summary] for train_summary in docs]

    # Remove all places in remove_these because city and state names are ruining the model
    docs = [[token for token in train_summary if token not in remove_these] for train_summary in docs]

    bigram = Phrases(docs, min_count = 10)
    for idx in range(len(docs)):
        for token in bigram[docs[idx]]:
            if '_' in token:
                # Token is a bigram, add it to the document
                docs[idx].append(token)
    
    return docs

def predict_category(model, new_summaries):
    """
    Predicts the category for a new summary or a 
    list of new summaries using the trained LDA model.

    Args:
        model (LdaModel): Trained LDA model.
        new_summaries (List[str] or str): New summary or list of new summaries to predict the category for.

    Returns:
        predicted_topics (List[int] or int): Predicted topic index or list of predicted topic indices for the new summaries.
    """
    dictionary = Dictionary.load('dictionary.pkl')
    topic_dictionary = {
                        0: "Politics",
                        1: "Hard News",
                        2: "Business",
                        3: "Entertainment",
                        4: "Community",
                        5: "Technology",
                        6: "Sports"
                        }
    # Processing the new summaries to prepare them for gensim
    processed_summaries = process_for_gensim(new_summaries)

    # Creating a bag of work representation of new summaries
    new_bow = [dictionary.doc2bow(summary) for summary in processed_summaries]

    #Predict the topic distribution
    predicted_topics = [max(model.get_document_topics(bow), key = lambda item: item[1])[0] for bow in new_bow]

    predicted_topics = [topic_dictionary[topic] for topic in predicted_topics]
    
    return predicted_topics

def camelcase_word(word):
    """
    This function creates a title into a title that can be displayed
    on the website

    Args:
        word (str): input word

    Returns:
        word (str): output capitalized word
    """
    if word.lower() in ['from', 'are', 'the', 'in', 'is']:
        return word.lower()
    elif word.isupper():
        return word
    else:
        return word.capitalize()

def process_title(title):
    """
    This function is made to remove non title punctuations
    makes all important words into camelcase and keeps words such as 
    for, in, the, are, is

    Args:
        title (str): The title of the articles

    Returns:
        processed_title (str): Processed Title to display on website
    """

    title = ''.join(char for char in title if ord(char)<128)

    title_words = title.split()
    processed_title = title_words[0]+' '+' '.join(camelcase_word(word) for word in title_words[1:])

    # Removing whitespace and period at the end of the sentence
    processed_title = re.sub(r'\s*\.\s*$', '', processed_title)
    processed_title = re.sub(r'\s+$', '', processed_title)

    return processed_title


def process_shrink_data(articles, location):
    """
    This function takes in the input that comes from a collection 
    in MongoDB. This function processes the important strings for
    each article in the document, removes any duplicate articles
    and adds a topic to each article using topic modeling model

    Arg:
        articles (List(json/dict)): A list of dictionaries/json where each json is an article
        location (str): The location used when querying to newscatcherAPI in the backend

    Returns:
        json(List(json))
    
    """
    
    # Loading the model and countvectorizer
    lda = LdaModel.load('model.pkl')


    location = location
    processed_articles = []
    
    for item in articles:
        
        #Condition to continue to next iteration if str present
        
        regex_pattern = rf'Reporting by .{{0,50}} in {location}'
        if re.search(regex_pattern, item["summary"]):
            continue
        
        # Get processed title
        title = process_title(item["title"])

        # Get excerpt
        if item["excerpt"] == None:
            excerpt = "No excerpt for this article"
        else:
            excerpt = process_string(item["excerpt"])
        
        
        processed_article = {
            "rank": int(item["rank"]),
            "location": location,
            "title": title,
            "excerpt": excerpt,
            "summary":item["summary"],
            "link": item["link"],
            "author": str(item["author"]),
            "published_date": item["published_date"][:10],
            "image_link": item["media"]
        }
        
        processed_articles.append(processed_article)

    articles_json = {
        "articles": processed_articles
    }

    data = articles_json['articles']
    print(len(data))

    unique_indices = get_unique_indices(data)

    articles_json['articles'] = [articles_json['articles'][i] for i in unique_indices]
    print("Unique indices filtered")
    print(len(articles_json["articles"]))
    
    summaries = [article['summary'] for article in articles_json['articles']]

    predictions = predict_category(model = lda, new_summaries=summaries)
    print("Predictions made")
    for article, prediction in zip(articles_json['articles'], predictions):
        
        article["topic"] = prediction
        print(article)

    #REMOVE BELOW PRINT STATEMENT WHEN DONE TESTING
    #print(len(articles_json['articles']))
    json_output = json.dumps(articles_json, ensure_ascii=False)
    #print(json_output)

    return json_output


Loading the data

In [126]:
with open("atl_test_data.json") as file:
    d = file.read()

    
data = json.loads(d)

test_data = []

for i in data:
    test_data.append(i)
   



In [142]:
process_shrink_data(test_data,"Atlanta, GA")

490
Unique indices filtered
488
Predictions made
{'rank': 1, 'location': 'Atlanta, GA', 'title': 'Pritzker Slams Desantis For Blocking AP Course', 'excerpt': 'With Assist From Olivia Olanderhappy Thursday Illinois On At The Present Time In 1967 A Report Setting Blizzard Struck Illinois', 'summary': "With assist from Olivia Olander\nHappy Thursday, Illinois. On at the present time in 1967, a report setting blizzard struck Illinois, dropping 23 inches of snow.\n\n\n\n\n\n\nIllinois Gov. JB Pritzker, left, criticizes Gov. Ron DeSantis and Florida Republicans for 'racist and homophobic legal guidelines' pertaining to AP Black historical past class. | Nam Y. Huh and Julia Nikhinson/AP Photo\n\n\n\n\nDemocratic Gov. JB Pritzker jumped into the tradition wars with Republican Gov. Ron DeSantis on Wednesday, criticizing Florida's resolution to remove an Advanced Placement highschool course on African American research from its curriculum.\nIn a pointed letter, Pritzker urged the nonprofit Colle

'{"articles": [{"rank": 1, "location": "Atlanta, GA", "title": "Pritzker Slams Desantis For Blocking AP Course", "excerpt": "With Assist From Olivia Olanderhappy Thursday Illinois On At The Present Time In 1967 A Report Setting Blizzard Struck Illinois", "summary": "With assist from Olivia Olander\\nHappy Thursday, Illinois. On at the present time in 1967, a report setting blizzard struck Illinois, dropping 23 inches of snow.\\n\\n\\n\\n\\n\\n\\nIllinois Gov. JB Pritzker, left, criticizes Gov. Ron DeSantis and Florida Republicans for \'racist and homophobic legal guidelines\' pertaining to AP Black historical past class. | Nam Y. Huh and Julia Nikhinson/AP Photo\\n\\n\\n\\n\\nDemocratic Gov. JB Pritzker jumped into the tradition wars with Republican Gov. Ron DeSantis on Wednesday, criticizing Florida\'s resolution to remove an Advanced Placement highschool course on African American research from its curriculum.\\nIn a pointed letter, Pritzker urged the nonprofit College Board that ove